In [1]:
#Used for displaying plots below the cell
%matplotlib inline
import math
import numpy as np
import pandas as pd
import scipy.stats as stats
import matplotlib.pyplot as plt

from collections import defaultdict
from scipy.stats.stats import pearsonr

In [2]:
df = pd.read_csv('customer_supermarket.csv', sep='\t', index_col=0)

In [3]:
df.head()

BasketID      BasketDate  Sale  CustomerID CustomerCountry  ProdID  \
0   536365  01/12/10 08:26  2,55     17850.0  United Kingdom  85123A   
1   536365  01/12/10 08:26  3,39     17850.0  United Kingdom   71053   
2   536365  01/12/10 08:26  2,75     17850.0  United Kingdom  84406B   
3   536365  01/12/10 08:26  3,39     17850.0  United Kingdom  84029G   
4   536365  01/12/10 08:26  3,39     17850.0  United Kingdom  84029E   

                             ProdDescr  Qta  
0   WHITE HANGING HEART T-LIGHT HOLDER    6  
1                  WHITE METAL LANTERN    6  
2       CREAM CUPID HEARTS COAT HANGER    8  
3  KNITTED UNION FLAG HOT WATER BOTTLE    6  
4       RED WOOLLY HOTTIE WHITE HEART.    6

The dataset seems to contain data about the shopping habits of the customers of a grocery store chain.  
Each row represents an object purchased:  
- BasketID: represents a batch of items bought at the same time, there can be more entries with the same BasketID  
- BasketDate: self explanatory, if the BasketID is the same between entries then also the BasketDate should stay the same  
- Sale: represents the value of the item, we need to figure out if it refers to a single item or the item*quantity
- CustomerID: identifies a unique customer
- ProdID: identifies a unique product for sale
- ProdDescr: describes the product
- Qta: number of items of the with id ProdID bought

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 471910 entries, 0 to 541909
Data columns (total 8 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   BasketID         471910 non-null  object 
 1   BasketDate       471910 non-null  object 
 2   Sale             471910 non-null  object 
 3   CustomerID       406830 non-null  float64
 4   CustomerCountry  471910 non-null  object 
 5   ProdID           471910 non-null  object 
 6   ProdDescr        471157 non-null  object 
 7   Qta              471910 non-null  int64  
dtypes: float64(1), int64(1), object(6)
memory usage: 32.4+ MB


Possibly interesting: the type of BasketID and Sale is not numerical

In [5]:
df.describe()

CustomerID            Qta
count  406830.000000  471910.000000
mean    15287.684160      10.716533
std      1713.603074     231.355136
min     12346.000000  -80995.000000
25%     13953.000000       1.000000
50%     15152.000000       4.000000
75%     16791.000000      12.000000
max     18287.000000   80995.000000

We need to fix the object situation in order to get a better understanding of the data set.

In [7]:
basketIdList = pd.to_numeric(df.BasketID, errors='coerce').isnull()

In [27]:
c_entry_count = 0
for i in range(basketIdList.size):
    if(basketIdList.iat[i] == True):
        data_v = df.iloc[i]
        print(data_v)
        c_entry_count += 1
print(c_entry_count)

BasketID                  C536379
BasketDate         01/12/10 09:41
Sale                         27,5
CustomerID                  14527
CustomerCountry    United Kingdom
ProdID                          D
ProdDescr                Discount
Qta                            -1
Name: 141, dtype: object
BasketID                                   C536383
BasketDate                          01/12/10 09:49
Sale                                          4,65
CustomerID                                   15311
CustomerCountry                     United Kingdom
ProdID                                      35004C
ProdDescr          SET OF 3 COLOURED  FLYING DUCKS
Qta                                             -1
Name: 154, dtype: object
BasketID                                  C536391
BasketDate                         01/12/10 10:24
Sale                                         1,65
CustomerID                                  17548
CustomerCountry                    United Kingdom
ProdID              

BasketID                        C538876
BasketDate               14/12/10 15:20
Sale                               2,95
CustomerID                        16499
CustomerCountry          United Kingdom
ProdID                            22272
ProdDescr          FELTCRAFT DOLL MARIA
Qta                                  -1
Name: 30569, dtype: object
BasketID                                      C538882
BasketDate                             14/12/10 15:56
Sale                                             1,25
CustomerID                                      12797
CustomerCountry                              Portugal
ProdID                                          21791
ProdDescr          VINTAGE HEADS AND TAILS CARD GAME 
Qta                                               -12
Name: 30853, dtype: object
BasketID                                      C538882
BasketDate                             14/12/10 15:56
Sale                                             1,25
CustomerID                      

BasketID                      C540634
BasketDate             10/01/11 12:02
Sale                             6,75
CustomerID                      13672
CustomerCountry        United Kingdom
ProdID                         79323P
ProdDescr          PINK CHERRY LIGHTS
Qta                                -4
Name: 51026, dtype: object
BasketID                            C540643
BasketDate                   10/01/11 14:08
Sale                                  10,95
CustomerID                            12471
CustomerCountry                     Germany
ProdID                                22423
ProdDescr          REGENCY CAKESTAND 3 TIER
Qta                                      -2
Name: 51157, dtype: object
BasketID                               C540652
BasketDate                      10/01/11 15:04
Sale                                     265,5
CustomerID                               17406
CustomerCountry                 United Kingdom
ProdID                                   22655
ProdDesc

Name: 70628, dtype: object
BasketID                                C542089
BasketDate                       25/01/11 12:39
Sale                                       2,55
CustomerID                                12681
CustomerCountry                          France
ProdID                                    22301
ProdDescr          COFFEE MUG CAT + BIRD DESIGN
Qta                                          -3
Name: 70650, dtype: object
BasketID                                C542089
BasketDate                       25/01/11 12:39
Sale                                       2,55
CustomerID                                12681
CustomerCountry                          France
ProdID                                    22300
ProdDescr          COFFEE MUG DOG + BALL DESIGN
Qta                                          -2
Name: 70651, dtype: object
BasketID                                 C542091
BasketDate                        25/01/11 12:41
Sale                                       12,75
Cust

Name: 80219, dtype: object
BasketID                              C543026
BasketDate                     02/02/11 14:44
Sale                                     9,95
CustomerID                              16717
CustomerCountry                United Kingdom
ProdID                                  22768
ProdDescr          FAMILY PHOTO FRAME CORNICE
Qta                                        -2
Name: 80220, dtype: object
BasketID                     C543026
BasketDate            02/02/11 14:44
Sale                            2,95
CustomerID                     16717
CustomerCountry       United Kingdom
ProdID                         21844
ProdDescr          RED RETROSPOT MUG
Qta                               -2
Name: 80221, dtype: object
BasketID                                   C543039
BasketDate                          02/02/11 16:31
Sale                                          1,25
CustomerID                                   16992
CustomerCountry                     United Kingdom


...

Name: 455288, dtype: object
BasketID                                    C575608
BasketDate                           10/11/11 12:38
Sale                                           4,25
CustomerID                                    16133
CustomerCountry                      United Kingdom
ProdID                                        22139
ProdDescr          RETROSPOT TEA SET CERAMIC 11 PC 
Qta                                              -3
Name: 455289, dtype: object
BasketID                               C575616
BasketDate                      10/11/11 12:51
Sale                                      4,15
CustomerID                               15805
CustomerCountry                 United Kingdom
ProdID                                   23469
ProdDescr          CARD HOLDER LOVE BIRD SMALL
Qta                                         -2
Name: 455407, dtype: object
BasketID                                C575616
BasketDate                       10/11/11 12:51
Sale                        

BasketID                                  C577073
BasketDate                         17/11/11 15:02
Sale                                         2,95
CustomerID                                  14359
CustomerCountry                    United Kingdom
ProdID                                      22698
ProdDescr          PINK REGENCY TEACUP AND SAUCER
Qta                                            -3
Name: 477726, dtype: object
BasketID                                C577075
BasketDate                       17/11/11 15:08
Sale                                       4,95
CustomerID                                14456
CustomerCountry                  United Kingdom
ProdID                                    22507
ProdDescr          MEMO BOARD RETROSPOT  DESIGN
Qta                                          -1
Name: 477744, dtype: object
BasketID                             C577081
BasketDate                    17/11/11 15:24
Sale                                     2,1
CustomerID               

BasketID                                     C578363
BasketDate                            24/11/11 10:40
Sale                                            3,75
CustomerID                                     15482
CustomerCountry                       United Kingdom
ProdID                                         22114
ProdDescr          HOT WATER BOTTLE TEA AND SYMPATHY
Qta                                              -24
Name: 497338, dtype: object
BasketID                              C578363
BasketDate                     24/11/11 10:40
Sale                                     4,25
CustomerID                              15482
CustomerCountry                United Kingdom
ProdID                                  22112
ProdDescr          CHOCOLATE HOT WATER BOTTLE
Qta                                       -24
Name: 497339, dtype: object
BasketID                                     C578363
BasketDate                            24/11/11 10:40
Sale                                          

Name: 516523, dtype: object
BasketID                           C579926
BasketDate                  01/12/11 09:19
Sale                                  1,65
CustomerID                           14389
CustomerCountry             United Kingdom
ProdID                               20727
ProdDescr          LUNCH BAG  BLACK SKULL.
Qta                                     -2
Name: 516524, dtype: object
BasketID                                 C579928
BasketDate                        01/12/11 09:29
Sale                                          25
CustomerID                                 14121
CustomerCountry                   United Kingdom
ProdID                                     23485
ProdDescr          BOTANICAL GARDENS WALL CLOCK 
Qta                                           -1
Name: 516549, dtype: object
BasketID                              C579929
BasketDate                     01/12/11 09:34
Sale                                     9,95
CustomerID                              17

BasketID                            C581228
BasketDate                   08/12/11 10:06
Sale                                  10,95
CustomerID                            16019
CustomerCountry              United Kingdom
ProdID                                22423
ProdDescr          REGENCY CAKESTAND 3 TIER
Qta                                      -6
Name: 536911, dtype: object
BasketID                                    C581228
BasketDate                           08/12/11 10:06
Sale                                           1,25
CustomerID                                    16019
CustomerCountry                      United Kingdom
ProdID                                        23210
ProdDescr          WHITE ROCKING HORSE HAND PAINTED
Qta                                             -12
Name: 536912, dtype: object
BasketID                               C581228
BasketDate                      08/12/11 10:06
Sale                                      2,95
CustomerID                         

In [9]:
basket_list = []
for i in range(basketIdList.size):
    if(basketIdList.iat[i] == True):
        data_v = df.iloc[i]
        basket_list.append(data_v.BasketID[0:3]) #Get the starting chars of each BasketID entry
        
print(set(basket_list)) #Get the unique values

{'C53', 'A56', 'C54', 'C56', 'C58', 'C55', 'C57'}


We can notice that a good chunk of the BasketID values start with a "C" instead of being just numbers and some start with "A" instead.

In [10]:
basket_c_list = []
basket_a_list = []
for i in range(basketIdList.size):
    if(basketIdList.iat[i] == True):
        data_v = df.iloc[i]
        if(data_v.BasketID[0] == "C"):
            basket_c_list.append(data_v)
        elif(data_v.BasketID[0] == "A"):
            basket_a_list.append(data_v)

In [21]:
print("Records starting with 'C':\n")
for entry in basket_c_list:
    print(entry)
    print("\n")

Records starting with 'C':

BasketID                  C536379
BasketDate         01/12/10 09:41
Sale                         27,5
CustomerID                  14527
CustomerCountry    United Kingdom
ProdID                          D
ProdDescr                Discount
Qta                            -1
Name: 141, dtype: object


BasketID                                   C536383
BasketDate                          01/12/10 09:49
Sale                                          4,65
CustomerID                                   15311
CustomerCountry                     United Kingdom
ProdID                                      35004C
ProdDescr          SET OF 3 COLOURED  FLYING DUCKS
Qta                                             -1
Name: 154, dtype: object


BasketID                                  C536391
BasketDate                         01/12/10 10:24
Sale                                         1,65
CustomerID                                  17548
CustomerCountry                    Uni

Name: 27367, dtype: object


BasketID                               C538536
BasketDate                      13/12/10 10:40
Sale                                      0,85
CustomerID                               15881
CustomerCountry                 United Kingdom
ProdID                                   22834
ProdDescr          HAND WARMER BABUSHKA DESIGN
Qta                                        -48
Name: 27389, dtype: object


BasketID                                     C538595
BasketDate                            13/12/10 12:03
Sale                                            2,55
CustomerID                                     15555
CustomerCountry                       United Kingdom
ProdID                                         82482
ProdDescr          WOODEN PICTURE FRAME WHITE FINISH
Qta                                               -2
Name: 27993, dtype: object


BasketID                       C538628
BasketDate              13/12/10 13:09
Sale                              2

Name: 45904, dtype: object


BasketID                            C540307
BasketDate                   06/01/11 12:58
Sale                                   1,25
CustomerID                            15823
CustomerCountry              United Kingdom
ProdID                                22094
ProdDescr          RED RETROSPOT TISSUE BOX
Qta                                     -12
Name: 45905, dtype: object


BasketID                       C540307
BasketDate              06/01/11 12:58
Sale                              1,25
CustomerID                       15823
CustomerCountry         United Kingdom
ProdID                           22093
ProdDescr          MOTORING TISSUE BOX
Qta                                -12
Name: 45906, dtype: object


BasketID                              C540307
BasketDate                     06/01/11 12:58
Sale                                      2,1
CustomerID                              15823
CustomerCountry                United Kingdom
ProdID             

Name: 72728, dtype: object


BasketID                        C542256
BasketDate               26/01/11 17:04
Sale                               1,06
CustomerID                        17722
CustomerCountry          United Kingdom
ProdID                            22095
ProdDescr          LADS ONLY TISSUE BOX
Qta                                  -1
Name: 72729, dtype: object


BasketID                                C542257
BasketDate                       26/01/11 17:06
Sale                                       7,95
CustomerID                                14341
CustomerCountry                  United Kingdom
ProdID                                    22841
ProdDescr          ROUND CAKE TIN VINTAGE GREEN
Qta                                          -2
Name: 72730, dtype: object


BasketID                      C542259
BasketDate             26/01/11 17:09
Sale                              8,5
CustomerID                      16656
CustomerCountry        United Kingdom
ProdID             

Name: 88128, dtype: object


BasketID                             C543772
BasketDate                    11/02/11 15:43
Sale                                    0,85
CustomerID                             13534
CustomerCountry               United Kingdom
ProdID                                 22355
ProdDescr          CHARLOTTE BAG SUKI DESIGN
Qta                                       -1
Name: 88129, dtype: object


BasketID                          C543773
BasketDate                 11/02/11 15:47
Sale                                 3,75
CustomerID                          12410
CustomerCountry               Switzerland
ProdID                              21218
ProdDescr          RED SPOTTY BISCUIT TIN
Qta                                    -1
Name: 88130, dtype: object


BasketID                        C543773
BasketDate               11/02/11 15:47
Sale                                8,5
CustomerID                        12410
CustomerCountry             Switzerland
ProdID           

...

Name: 400733, dtype: object


BasketID                                C571346
BasketDate                       17/10/11 11:46
Sale                                       1,45
CustomerID                                16101
CustomerCountry                  United Kingdom
ProdID                                    22969
ProdDescr          HOMEMADE JAM SCENTED CANDLES
Qta                                          -1
Name: 400734, dtype: object


BasketID                   C571440
BasketDate          17/10/11 13:31
Sale                        495,98
CustomerID                   14096
CustomerCountry     United Kingdom
ProdID                        CRUK
ProdDescr          CRUK Commission
Qta                             -1
Name: 401767, dtype: object


BasketID                            C571466
BasketDate                   17/10/11 14:31
Sale                                   1,25
CustomerID                            16463
CustomerCountry              United Kingdom
ProdID                    



BasketID                                 C573283
BasketDate                        28/10/11 13:57
Sale                                        9,95
CustomerID                                 18030
CustomerCountry                   United Kingdom
ProdID                                     22776
ProdDescr          SWEETHEART 3 TIER CAKE STAND 
Qta                                           -1
Name: 424728, dtype: object


BasketID                                 C573306
BasketDate                        28/10/11 16:15
Sale                                        9,95
CustomerID                                 17837
CustomerCountry                   United Kingdom
ProdID                                     22796
ProdDescr          PHOTO FRAME 3 CLASSIC HANGING
Qta                                           -1
Name: 425161, dtype: object


BasketID                                      C573306
BasketDate                             28/10/11 16:15
Sale                                          

Name: 455513, dtype: object


BasketID                                     C575626
BasketDate                            10/11/11 13:21
Sale                                            4,95
CustomerID                                     17651
CustomerCountry                       United Kingdom
ProdID                                         22720
ProdDescr          SET OF 3 CAKE TINS PANTRY DESIGN 
Qta                                               -1
Name: 455514, dtype: object


BasketID                                       C575630
BasketDate                              10/11/11 13:35
Sale                                              4,25
CustomerID                                       15830
CustomerCountry                         United Kingdom
ProdID                                          84029G
ProdDescr          KNITTED UNION FLAG HOT WATER BOTTLE
Qta                                                 -2
Name: 455574, dtype: object


BasketID                              C575630


Name: 490508, dtype: object


BasketID                  C578073
BasketDate         22/11/11 16:02
Sale                         0,32
CustomerID                  18139
CustomerCountry    United Kingdom
ProdID                          M
ProdDescr                  Manual
Qta                           -36
Name: 491655, dtype: object


BasketID                  C578073
BasketDate         22/11/11 16:02
Sale                         0,56
CustomerID                  18139
CustomerCountry    United Kingdom
ProdID                          M
ProdDescr                  Manual
Qta                           -36
Name: 491656, dtype: object


BasketID                  C578076
BasketDate         22/11/11 16:18
Sale                         0,56
CustomerID                  18139
CustomerCountry    United Kingdom
ProdID                          M
ProdDescr                  Manual
Qta                           -24
Name: 491886, dtype: object


BasketID                                     C578077
BasketDate 

Name: 529658, dtype: object


BasketID                                 C580740
BasketDate                        06/12/11 09:25
Sale                                        1,25
CustomerID                                 12479
CustomerCountry                          Germany
ProdID                                     20979
ProdDescr          36 PENCILS TUBE RED RETROSPOT
Qta                                          -12
Name: 529659, dtype: object


BasketID                      C580741
BasketDate             06/12/11 09:29
Sale                             2,08
CustomerID                      17659
CustomerCountry        United Kingdom
ProdID                          23084
ProdDescr          RABBIT NIGHT LIGHT
Qta                                -2
Name: 529660, dtype: object


BasketID                                 C580741
BasketDate                        06/12/11 09:29
Sale                                        9,95
CustomerID                                 17659
CustomerCountry   

In [18]:
print("Records starting with 'A':\n")
for entry in basket_a_list:
    print(entry)
    print("\n")

Records starting with 'A':

BasketID                   A563186
BasketDate          12/08/11 14:51
Sale                     -11062,06
CustomerID                     NaN
CustomerCountry     United Kingdom
ProdID                           B
ProdDescr          Adjust bad debt
Qta                              1
Name: 299983, dtype: object


BasketID                   A563187
BasketDate          12/08/11 14:52
Sale                     -11062,06
CustomerID                     NaN
CustomerCountry     United Kingdom
ProdID                           B
ProdDescr          Adjust bad debt
Qta                              1
Name: 299984, dtype: object




There seems to be a strong correlation between the "C" and a negative quantity, this could indicate a customer that asked for a refund.  

There is also some interesting correlation between the "A" start and a ProdDescr containing "Adjust bad debt", maybe the "A" stands for adjust and since the CustomerId in both cases is NaN this could be an operation that concerns only the management of the shop and not something that concerns the customers (which I assume is our primary objective).  
Or maybe a cashier made a mistake by typing a wrong number in the cash register and fixed it with this new operation.  

Let's investigate the "C" hypothesis.

In [64]:
neg_qta = df.loc[df['Qta'] < 0]
neg_c_qta = df.loc[df["BasketID"].str.contains("C")]
print("Total entries with negative Qta: " + str(len(neg_qta)))
print("Total entries with C in BasketID and negative Qta: " + str(len(neg_c_qta)))


Total entries with negative Qta: 9752
Total entries with C in BasketID and negative Qta: 9084


In [69]:
neg_qta_wo_C = neg_qta.drop(neg_c_qta.index)
len(neg_qta_wo_C)

668